In [21]:
import matplotlib.pyplot as plt # For plotting
import numpy as np              # Linear algebra library
import pandas as pd

Use pandas to read the dataset.

In [22]:
! pwd
expr_df = pd.read_csv("../metadata/length_and_depth.csv")
expr_df = expr_df.drop("nvar", axis=1)
expr_df = expr_df.rename(columns={
    "length" : "expr_length",
    "depth" : "expr_depth"
})
expr_df

/Users/felixgao/Desktop/Year3/STA378/OptimizationParameterTuning/Julia Notebook/src


problem        objtype  variable_nvar  expr_length  expr_depth
0        NZF1  least_squares           True          250           8
1     arglina  least_squares           True        10404           9
2     arglinb  least_squares           True        40200           8
3     arglinc          other           True        39204           7
4     argtrig          other           True          497           7
..        ...            ...            ...          ...         ...
100    tridia          other           True          398           6
101    vardim          other           True          798           6
102  vibrbeam  least_squares          False          481          13
103    watson  least_squares          False         3900          12
104     woods          other           True          425           7

[105 rows x 5 columns]

In [23]:
complete_df = pd.read_csv("../results/complete_dataset_as_of_nov6.csv")
complete_df = complete_df[complete_df["is_init_run"] == 0]
complete_df = complete_df.rename(columns={"name" : "problem"})
df = complete_df.merge(
    expr_df,
    on = 'problem',
    how = "inner"
)
df

status problem       solver  mem  nvar      time    memory  \
0      first_order    NZF1  LBFGSSolver    1    91  1.409402  0.125416   
1      first_order    NZF1  LBFGSSolver    2    91  1.407668  0.095296   
2      first_order    NZF1  LBFGSSolver    3    91  1.407882  0.103456   
3      first_order    NZF1  LBFGSSolver    4    91  1.407476  0.098352   
4      first_order    NZF1  LBFGSSolver    5    91  1.407906  0.108416   
...            ...     ...          ...  ...   ...       ...       ...   
18821  first_order   woods  LBFGSSolver   96  1000  1.482090  3.197624   
18822  first_order   woods  LBFGSSolver   97  1000  1.481800  3.229800   
18823  first_order   woods  LBFGSSolver   98  1000  1.482000  3.261976   
18824  first_order   woods  LBFGSSolver   99  1000  1.481908  3.294152   
18825  first_order   woods  LBFGSSolver  100  1000  1.483005  3.326648   

       num_iter  nvmops  neval_obj  ...  neval_grad  init_eval_grad_time  \
0           287     287        328  ...         315             0.000031   
1           199     199        223  ...         216             0.000019   
2           213     213        234  ...         228             0.000016   
3           191     191        209  ...         203             0.000017   
4           209     209        231  ...         225             0.000017   
...         ...     ...        ...  ...         ...                  ...   
18821        64      64         84  ...          75             0.001356   
18822        64      64         84  ...          75             0.001373   
18823        64      64         84  ...          75             0.001367   
18824        64      64         84  ...          75             0.001358   
18825        64      64         84  ...          75             0.001365   

       init_eval_grad_mem  init_eval_grad_alloc  is_init_run  is_scalable  \
0                0.001440                     5        False        False   
1                0.001440                     5        False        False   
2                0.001440                     5        False        False   
3                0.001440                     5        False        False   
4                0.001440                     5        False        False   
...                   ...                   ...          ...          ...   
18821            0.008664                     5        False         True   
18822            0.008664                     5        False         True   
18823            0.008664                     5        False         True   
18824            0.008664                     5        False         True   
18825            0.008664                     5        False         True   

             objtype  variable_nvar  expr_length expr_depth  
0      least_squares           True          250          8  
1      least_squares           True          250          8  
2      least_squares           True          250          8  
3      least_squares           True          250          8  
4      least_squares           True          250          8  
...              ...            ...          ...        ...  
18821          other           True          425          7  
18822          other           True          425          7  
18823          other           True          425          7  
18824          other           True          425          7  
18825          other           True          425          7  

[18826 rows x 23 columns]

In [24]:
# from sklearn.tree import DecisionTreeClassifier

# X = df_problem_level[[
#     "nvar", 
#     "expr_length", 
#     "expr_depth", 
#     "init_eval_obj_time", 
#     "init_eval_obj_mem",
#     "init_eval_obj_alloc",
#     "init_eval_grad_time",
#     "init_eval_grad_mem",
#     "init_eval_grad_alloc"
# ]].values
# y = df_problem_level["mem"].values     # categorical / integer

# clf = DecisionTreeClassifier(max_depth=5, random_state=0)
# clf.fit(X, y)

In [25]:
problems = df["problem"].unique()
rng = np.random.default_rng(seed=42)
rng.shuffle(problems)

n = len(problems)
n_train = int(0.7 * n)
n_valid = int(0.15 * n)

train_problems = problems[:n_train]
valid_problems = problems[n_train:n_train + n_valid]
test_problems  = problems[n_train + n_valid:]

train_df = df[df["problem"].isin(train_problems)].reset_index(drop=True)
valid_df = df[df["problem"].isin(valid_problems)].reset_index(drop=True)
test_df  = df[df["problem"].isin(test_problems)].reset_index(drop=True)

In [26]:
from sklearn.tree import DecisionTreeRegressor
feature_cols = ["nvar", 
                "expr_length", 
                "expr_depth", 
                "mem",
                "init_eval_obj_time", 
                "init_eval_obj_mem",
                "init_eval_obj_alloc",
                "init_eval_grad_time",
                "init_eval_grad_mem",
                "init_eval_grad_alloc"]
target_col = "time"
X_train = train_df[feature_cols].to_numpy(dtype=float)
X_valid = valid_df[feature_cols].to_numpy(dtype=float)
X_test  = test_df[feature_cols].to_numpy(dtype=float)

t_train = np.log1p(train_df[target_col].to_numpy(dtype=float))
t_valid = np.log1p(valid_df[target_col].to_numpy(dtype=float))
t_test  = np.log1p(test_df[target_col].to_numpy(dtype=float))

In [27]:
from sklearn.tree import DecisionTreeRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
import numpy as np

# log1p transform of targets
y_train = np.log1p(t_train)
y_valid = np.log1p(t_valid)

best_tree = None
best_score = np.inf
best_params = None

for max_depth in [3, 5, 7, 9, None]:
    for min_leaf in [1, 3, 5, 10]:
        tree = DecisionTreeRegressor(
            max_depth=max_depth,
            min_samples_leaf=min_leaf,
            random_state=0,
        )
        tree.fit(X_train, y_train)

        pred_valid_log = tree.predict(X_valid)
        mse_valid = mean_squared_error(y_valid, pred_valid_log)

        if mse_valid < best_score:
            best_score = mse_valid
            best_tree = tree
            best_params = (max_depth, min_leaf)
            print(
                "New best:",
                "depth =", max_depth,
                "min_leaf =", min_leaf,
                "log1p MSE =", mse_valid,
            )
        else:
            print(
                "depth =", max_depth,
                "min_leaf =", min_leaf,
                "log1p MSE =", mse_valid,
            )

print("Best validation log1p MSE (tree):", best_score)
print("Best params (max_depth, min_leaf):", best_params)


New best: depth = 3 min_leaf = 1 log1p MSE = 0.15632530489531712
depth = 3 min_leaf = 3 log1p MSE = 0.15632530489531712
depth = 3 min_leaf = 5 log1p MSE = 0.15632530489531712
depth = 3 min_leaf = 10 log1p MSE = 0.15632530489531712
New best: depth = 5 min_leaf = 1 log1p MSE = 0.11042393090233647
New best: depth = 5 min_leaf = 3 log1p MSE = 0.10995887971445993
New best: depth = 5 min_leaf = 5 log1p MSE = 0.10986077459236172
New best: depth = 5 min_leaf = 10 log1p MSE = 0.10977529188608122
New best: depth = 7 min_leaf = 1 log1p MSE = 0.10388330361127261
New best: depth = 7 min_leaf = 3 log1p MSE = 0.10331416346438081
depth = 7 min_leaf = 5 log1p MSE = 0.10484287124097805
New best: depth = 7 min_leaf = 10 log1p MSE = 0.1016825371553976
depth = 9 min_leaf = 1 log1p MSE = 0.11743191194314279
depth = 9 min_leaf = 3 log1p MSE = 0.10519614215267752
depth = 9 min_leaf = 5 log1p MSE = 0.10678514095147619
depth = 9 min_leaf = 10 log1p MSE = 0.11853141608138308
depth = None min_leaf = 1 log1p MSE =

In [28]:
best_depth, best_min_leaf = best_params

X_train_full = np.vstack([X_train, X_valid])
t_train_full = np.concatenate([t_train, t_valid])
y_train_full = np.log1p(t_train_full)

final_tree = DecisionTreeRegressor(
    max_depth=best_depth,
    min_samples_leaf=best_min_leaf,
    random_state=0,
)
final_tree.fit(X_train_full, y_train_full)

# test regression metrics in real time units
pred_test_log = final_tree.predict(X_test)
pred_test_time = np.expm1(pred_test_log)

test_mse = mean_squared_error(t_test, pred_test_time)
test_mae = mean_absolute_error(t_test, pred_test_time)
test_r2  = r2_score(t_test, pred_test_time)

print("Tree Test MSE (time):", test_mse)
print("Tree Test MAE (time):", test_mae)
print("Tree Test R^2 (time):", test_r2)


Tree Test MSE (time): 1.4885923564714536
Tree Test MAE (time): 0.6964968473662566
Tree Test R^2 (time): 0.2725535216700501


In [29]:
problem_feature_cols = [c for c in feature_cols if c != "mem"]

def choose_best_mem(model, x_problem, mem_candidates):
    preds = []
    for mem in mem_candidates:
        x = np.concatenate([x_problem, [mem]])
        preds.append((mem, model.predict(x.reshape(1, -1))[0]))
    return min(preds, key=lambda x: x[1])

In [30]:
problem_feature_cols = [c for c in feature_cols if c != "mem"]
mem_candidates_global = np.sort(train_df["mem"].unique())

In [35]:
def evaluate_mem_selector(model, df_split):
    rows = []

    # treat (problem, nvar) as one instance
    for (prob, nvar), group in df_split.groupby(["problem", "nvar"]):
        mems_available = np.sort(group["mem"].unique())
        mem_candidates = [m for m in mem_candidates_global if m in mems_available]
        if not mem_candidates:
            continue

        # build x_problem without mem
        row0 = group.iloc[0]
        x_problem = row0[problem_feature_cols].to_numpy(dtype=float)

        # this is where you use choose_best_mem
        mem_pred, _ = choose_best_mem(model, x_problem, mem_candidates)

        # true best mem and time for this instance
        best_row = group.loc[group["time"].idxmin()]
        mem_best = best_row["mem"]
        time_best = best_row["time"]

        # actual time if we use mem_pred
        time_chosen = group.loc[group["mem"] == mem_pred, "time"].min()

        rows.append(
            {
                "problem": prob,
                "nvar": nvar,
                "mem_pred": mem_pred,
                "mem_best": mem_best,
                "time_best": time_best,
                "time_chosen": time_chosen,
            }
        )

    res = pd.DataFrame(rows)
    if len(res) == 0:
        return res, float("nan"), float("nan")

    frac_exact = (res["mem_pred"] == res["mem_best"]).mean()
    avg_ratio = (res["time_chosen"] / res["time_best"]).mean()
    return res, frac_exact, avg_ratio

In [32]:

test_res_tree, frac_exact_tree, avg_ratio_tree = evaluate_mem_selector(final_tree, test_df)

ratio_tree = test_res_tree["time_chosen"] / test_res_tree["time_best"]

print("Tree exact match fraction:", frac_exact_tree)
print("Tree avg time_chosen / time_best:", avg_ratio_tree)
print("Tree median time_chosen / time_best:", ratio_tree.median())
print("Tree frac within 5%:", (ratio_tree <= 1.05).mean())
print("Tree frac within 10%:", (ratio_tree <= 1.10).mean())


Tree exact match fraction: 0.03225806451612903
Tree avg time_chosen / time_best: 6.372046487416427
Tree median time_chosen / time_best: 1.065039775561972
Tree frac within 5%: 0.4838709677419355
Tree frac within 10%: 0.5161290322580645


In [41]:
import matplotlib.pyplot as plt
from sklearn import tree

plt.figure(figsize=(500, 100))
tree.plot_tree(
    final_tree,
    feature_names=feature_cols,
    filled=True,
    rounded=True,
    max_depth=7,   
    fontsize=10,
)
plt.tight_layout()
plt.show()


In [37]:
from sklearn.tree import export_graphviz

export_graphviz(
    final_tree,
    out_file="regression_tree.dot",
    feature_names=feature_cols,
    filled=True,
    rounded=True,
    max_depth=3,          # again, for readability
)

# then in a terminal (if you have graphviz installed):
# dot -Tpdf regression_tree.dot -o regression_tree.pdf
